In [14]:
import requests
import time

import random
pages = [
            random.randint(1, 968000015)
            for _ in range(500)
        ]
# print(pages)

base_url = "https://datasets-server.huggingface.co/rows"
params = {
            "dataset": "tiiuae/falcon-refinedweb",
            "config": "default",
            "split": "train",
        }
# response = requests.get(base_url, params=params)
# response.raise_for_status()
# for row in response.json()["rows"]:
#   content = row["row"]["content"]
num_rows_per_page = 100
retry_limit = 10
retry_delay = 5
Falcon = []

print('Started Fetching Data')
def fetch_data_for_page(page):
        params["offset"] = page
        params["limit"] = num_rows_per_page
        attempt = 0
        while attempt < retry_limit:
            try:
                response = requests.get(base_url, params=params)
                response.raise_for_status()  # This will raise an HTTPError if the HTTP request returned an unsuccessful status code
                for row in response.json()["rows"]:
                    content = row["row"]["content"]
                    Falcon.append(content)
                len(Falcon)
                #print(f"Fetched data for all the Pages.")
                break
            except requests.exceptions.HTTPError as e:
                attempt += 1
                print(
                    f"Failed to fetch data, retrying. Attempt {attempt}/{retry_limit}"
                )
                if attempt < retry_limit:
                    time.sleep(retry_delay)  # Wait before the next retry
                else:
                    print(
                        "Maximum retry limit reached. Unable to fetch data."
                    )
                    raise

for page in pages:
  fetch_data_for_page(page)

print(f"Fetched data for all the Pages.")

Started Fetching Data
Failed to fetch data, retrying. Attempt 1/10
Failed to fetch data, retrying. Attempt 1/10
Fetched data for all the Pages.


In [15]:
import csv

# Open the CSV file for writing
with open("FalconData2.csv", "w", newline="") as csvfile:
    # Create a CSV writer object
    writer = csv.writer(csvfile)

    # Write the header row
    writer.writerow(["Text"])

    # Write each element in the list as a row in the CSV file
    for element in Falcon:
        writer.writerow([element])


In [30]:
import pandas as pd

# Read the CSV file into a pandas DataFrame
df = pd.read_csv("FalconData2.csv")

# Check for duplicate rows
duplicate_rows = df[df.duplicated()]

# Print the number of duplicate rows
print(f"Number of duplicate rows: {len(duplicate_rows)}")

# Print the duplicate rows
print(duplicate_rows)

Number of duplicate rows: 5
                                                   Text
522                                               Name:
11746  Description.\nReviews\nThere are no reviews yet.
17606  Description.\nReviews\nThere are no reviews yet.
30436                                               NaN
42549                                               !\n


In [31]:
df.head()

Text
0   […]\nM&S bank […]\nLowest unsecured loan rate...
1  JavaScript seems to be disabled in your browse...
2  CMTech has designed a game to foster social in...
3  A Storyteller's Point of View\nMy\nWriting\nLe...
4  mspu.us was registered 1 decade 3 years ago. I...

In [32]:
df.tail()

Text
49995  Alumni in Action: Grace Heyne Lybrand\nWhen Gr...
49996  This.\n51.351813 -105.220438\n12 replies on “L...
49997  VIDEO 1: Panel discussion with John Nichols, a...
49998  The Prototype DA-2A made its first flight on M...
49999  default search action\nBibTeX record journals/...

In [33]:
# Calculate the word count for each row without storing it as a column
word_counts = df['Text'].apply(lambda x: len(str(x).split()))


print("Number of Words:")
print(word_counts)

# print("Smallest Count")
# print(word_counts.min())

# print("Largest Count")
# print(word_counts.max())

# Find the row with the smallest word count
smallest_row = df.loc[word_counts.idxmin()]

# Find the row with the largest word count
largest_row = df.loc[word_counts.idxmax()]

# Display the smallest and largest rows
print("Smallest Row:")
print(smallest_row)

print("\nLargest Row:")
print(largest_row)


Number of Words:
0         65
1         79
2        287
3        302
4        130
        ... 
49995     64
49996    325
49997     58
49998    623
49999     67
Name: Text, Length: 50000, dtype: int64
Smallest Row:
Text    This
Name: 270, dtype: object

Largest Row:
Text    MAMMALS\n400. Abu Jafar, M.Z., and C. Hays-Sha...
Name: 33020, dtype: object


In [34]:
target_row=30436
specific_row = df.iloc[target_row]
specific_row

Text    NaN
Name: 30436, dtype: object

In [13]:
print(specific_row)

Text    The old wireline Bell telephone system was bui...
Name: 19995, dtype: object


In [14]:
print(specific_row.to_string())

Text    The old wireline Bell telephone system was bui...


In [17]:
print(len(specific_row.to_string()))

57


In [24]:
# import pandas as pd

# # Load the dataset
# df = pd.read_csv("FalconData2.csv")

# # Calculate the index to split the data at the last 10%
# split_index = int(len(df) * 0.980)

# # Split the data into training and validation sets
# train_df = df.iloc[:split_index]  # First 90% for training
# validation_df = df.iloc[split_index:]  # Last 10% for validation

# # Display the sizes of the training and validation sets
# print(f"Training set size: {len(train_df)}")
# print(f"Validation set size: {len(validation_df)}")

# # Optionally, save the datasets to new CSV files
# train_df.to_csv("FalconData_train2.csv", index=False)
# validation_df.to_csv("FalconData_validation2.csv", index=False)


Training set size: 49000
Validation set size: 1000


In [35]:
import pandas as pd

# Load the dataset
df = pd.read_csv("FalconData2.csv")

# Check for NaN values and remove rows with NaN values
# df = df.dropna()
original_length = len(df)

df = df.dropna()

removed_rows = original_length - len(df)
print(f"Number of rows removed due to NaN values: {removed_rows}")

# Calculate the index to split the data at the last 2%
split_index = int(len(df) * 0.98)

# Split the data into training and validation sets
train_df = df.iloc[:split_index]  # First 98% for training
validation_df = df.iloc[split_index:]  # Last 2% for validation

# Display the sizes of the training and validation sets
print(f"Training set size: {len(train_df)}")
print(f"Validation set size: {len(validation_df)}")

# Save the datasets to new CSV files
train_df.to_csv("FalconData_train2.csv", index=False)
validation_df.to_csv("FalconData_validation2.csv", index=False)


Number of rows removed due to NaN values: 2
Training set size: 48998
Validation set size: 1000


In [36]:
# Read the CSV file into a pandas DataFrame
df1 = pd.read_csv("FalconData_train2.csv")

# Check for duplicate rows
duplicate_rows1 = df1[df1.duplicated()]

# Print the number of duplicate rows
print(f"Number of duplicate rows: {len(duplicate_rows1)}")

# Print the duplicate rows
print(duplicate_rows1)

Number of duplicate rows: 4
                                                   Text
522                                               Name:
11745  Description.\nReviews\nThere are no reviews yet.
17605  Description.\nReviews\nThere are no reviews yet.
42547                                               !\n


In [26]:
df1.head()

Text
0   […]\nM&S bank […]\nLowest unsecured loan rate...
1  JavaScript seems to be disabled in your browse...
2  CMTech has designed a game to foster social in...
3  A Storyteller's Point of View\nMy\nWriting\nLe...
4  mspu.us was registered 1 decade 3 years ago. I...

In [27]:
df1.tail()

Text
48995  A Chenango County man was charged Wednesday wi...
48996  2-Tone Black Personalized Embroidered One Init...
48997  NARAL Pro-Choice America PAC Endorses Colleen ...
48998  Posts Tagged by Thomas Paine\nAEI Hosts Peter ...
48999  Pantry feeds families in need\n- Details\n- Ca...